In [1]:
using DelimitedFiles
using Plots
plotly()
using FFTW;

┌ Info: For saving to png with the Plotly backend PlotlyBase has to be installed.
└ @ Plots C:\Users\Dayalan\.julia\packages\Plots\HcxwM\src\backends.jl:435


In [2]:
N = 5000#175e3
fs = 125e6
Δt = 1/fs
t = 0:Δt:(N -1)/fs; 

In [ ]:
function f_ax(p)
    n = length(p)
    Δf = 1/(n*Δt)
    if mod(n,2)==0    # case N even
        return (-n/2:n/2-1)*Δf;    
    else   # case N odd
        return (-(n-1)/2 : (n-1)/2)*Δf; 
    end
end

In [4]:
rect(t) = (abs.(t).<=0.5)*1.0;
T_pulse = 15e-6
mc_pulse(t) = A*sin.(ω0*(t.-T_pulse/2)).*rect((t.-T_pulse/2)./T_pulse); 
fc = 15e5
B = 20e5
k = B/T_pulse
chirp(t) = cos(2*pi*(fc*(t-T_pulse/2) + 0.5*k*(t-T_pulse/2)^2))*rect((t-T_pulse/2)/T_pulse);

td = 2*1000/3e8 #target at 1km

v = chirp.(t)
v_d = chirp.(t.-3*td)

p1 = plot(t.*10e6,v_d, legend = false)
#title!("Simulated delayed chirp")
xlabel!("Time (μs)")
ylabel!("Amplitude")

#display(plot())
#A chirp and delayed version generated arbitrarily illustrate the concept. Specific parameters used are described in method


In [ ]:
#FT of recv sig
V_D = fft(v_d)

#matched filter
V = fft(v)
H = conj.(V) 

#Apply mf
Y = H.*V_D
y = ifft(Y)


p3 = plot(f_ax(V),fftshift(abs.(V)), legend = false, ticks=:native)
#plot!(f_ax(V),fftshift(abs.(V_D)))
#title!("Chirp magnitude response")
xlabel!("Frequency (Hz)")
ylabel!("Magnitude")
display(p3)

p1 = plot(t.*10e6,real(y), legend = false)
#title!("Matched filter output v. Time")
xlabel!("Time (μs)")
ylabel!("Amplitude")

display(p1)
p2 = plot(t*3e8/2,real(y), legend = false)
#title!("Matched filter output v. Distance")
xlabel!("Distance (m)")
ylabel!("Amplitude")

display(p2)
#p1 = plot(f_ax(Y),fftshift(abs.(Y)), label = ["chirp" "delayed chirp"])
#title!("Simulated chirp and delayed chirp")
##xlabel!("Time (μs)")
#ylabel!("Amplitude")

In [6]:
#Noise
using Statistics
σ = 1
n = σ * randn(N); # Create the random samples with std dev of σ.
p4 = plot(n)

In [7]:
vn = chirp.(t) + n
v_dn = chirp.(t.-3*td) + n
#EVEN when creating a matched filter from a noisy signal it still works
p1 = plot(t.*10e6, v_dn, legend = false)
#title!("Delayed chirp buried in noise")
xlabel!("Time (μs)")
ylabel!("Amplitude")
display(p1)
#FT of recv sig
V_DN = fft(v_dn)

#matched filter
VN = fft(vn)
Hn = conj.(VN) 

#Apply mf
YN = H.*V_DN
yn = ifft(YN)

p2 = plot(t[2:end]*3e8/2,real(yn[2:end]), legend = false)
#title!("Matched filter output v. Distance")
xlabel!("Distance (m)")
ylabel!("Amplitude")
#Mention how stacking can improve!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!

LoadError: UndefVarError: H not defined

In [22]:
#STACKINGGG
stack = zeros(N)

for i in 1:5
    noise = randn(N);
    v3 = 2*chirp.(t.-3*td) .+ noise
    stack = stack .+ v3
end

#stack = 5*chirp.(t.-3*td) + n
p7 = plot(t.*10e6, stack, legend = false)
title!("5 signal stacks of a delayed chirp buried in noise")
xlabel!("Time (μs)")
ylabel!("Amplitude")
display(p7)
#large amplitude

stack2 = zeros(N)
ns = zeros(N)
for i in 1:1000
    noise = randn(N);
    ns = ns.+noise
    v3 = chirp.(t.-3*td) .+ noise
    stack2 = stack2 .+ v3
end
p8 = plot(t.*10e6, stack2, legend = false)
title!("Delayed chirp with amplitude increased by factor of 5")
xlabel!("Time (μs)")
ylabel!("Amplitude")
display(p8)

pw = plot(ns)
display(pw)
x3= 100*chirp.(t.-3*td)+n

p9 = plot(t.*10e6, x3, legend = false)
title!("Delayed chirp with amplitude increased by factor of 5")
xlabel!("Time (μs)")
ylabel!("Amplitude")
display(p9)